In [1]:
import nltk
from typing import Tuple
from datasets import load_dataset, DatasetDict, load_from_disk
from transformers import DataCollatorForSeq2Seq, AutoTokenizer, AutoModelForSeq2SeqLM

#from config import DataConfig
from loguru import logger

nltk.download("punkt")
nltk.download("punkt_tab")

[nltk_data] Downloading package punkt to /home/petar/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package punkt_tab to /home/petar/nltk_data...
[nltk_data]   Package punkt_tab is already up-to-date!


True

In [9]:
dev = False
dataset_path = "smartcat/Amazon-2023-GenQ"
dataset_subset = ""
cache_dir = "./cache_dir_test"


In [13]:
if dev:
    split_percentage = "[:3%]"
else:
    split_percentage=""   

train_subset = load_dataset(dataset_path, name=dataset_subset, cache_dir=cache_dir, split="train"+split_percentage)
test_subset = load_dataset(dataset_path, name=dataset_subset, cache_dir=cache_dir, split="test"+split_percentage)       
dataset_hf = DatasetDict(
    {
        "train": train_subset,
        "test": test_subset,
    }
)
logger.info(f'Selected sample rows for "train" and test sample for "test"') 

2025-02-12 10:07:58.492 | INFO     | __main__:<module>:14 - Selected sample rows for "train" and test sample for "test"


In [14]:
dataset_hf["test"]

Dataset({
    features: ['parent_asin', 'main_category', 'title', 'description', 'features', 'embellished_description', 'brand', 'images', 'short_query', 'long_query'],
    num_rows: 25706
})

In [20]:
dataset_path = "smartcat/Amazon-2023-GenQ"
dataset_subset = ""
input_text_column = ["title", "description"]
label_text_column = "short_query"
#load_tokenized_dataset = False
#save_tokenized_dataset= True
max_input_length = 512
max_target_length = 30
cache_dir = "./cache_dir_test"
dev= True

In [21]:
import nltk
from typing import Tuple
from datasets import load_dataset, DatasetDict, load_from_disk
from transformers import DataCollatorForSeq2Seq, AutoTokenizer, AutoModelForSeq2SeqLM, T5Tokenizer

#from config import DataConfig
from loguru import logger
tokenizer = T5Tokenizer.from_pretrained("BeIR/query-gen-msmarco-t5-base-v1")
nltk.download("punkt")
nltk.download("punkt_tab")

def preprocess_function(examples):
    """
    Tokenizes input and target text while ensuring proper truncation.

    Args:
        examples (dict): A batch of dataset samples.

    Returns:
        dict: Tokenized inputs and labels.
    """
    input_texts = [
        "\n\n".join(
            str(examples[col][i]) if col in examples and examples[col][i] is not None else ""
            for col in input_text_column
        ).strip()
        for i in range(len(examples[input_text_column[0]]))  # Iterate over batch elements
    ]
    print(type(input_texts))
    print(input_texts)
    model_inputs = tokenizer(
        input_texts,
        max_length=max_input_length,
        truncation=True,
        padding = "max_length"
    )

    labels = tokenizer(
        examples[label_text_column], max_length=max_target_length, truncation=True, padding="max_length"
    )
    model_inputs["labels"] = labels["input_ids"]
    return model_inputs


logger.info(f"Loaded dataset: {dataset_path}, name={dataset_subset}")

if dev:
    split_percentage = "[:3%]"
else:
    split_percentage=""   

train_subset = load_dataset(dataset_path, name=dataset_subset, cache_dir=cache_dir, split="train"+split_percentage)
test_subset = load_dataset(dataset_path, name=dataset_subset, cache_dir=cache_dir, split="test"+split_percentage)       
dataset_hf = DatasetDict(
    {
        "train": train_subset,
        "test": test_subset,
    }
)
logger.info('Selected  rows for "train" and for "test"') 
# 
tokenized_datasets = dataset_hf.map(preprocess_function, batched=True)
logger.info("Finished preprocessing tokenized dataset.")
print(tokenized_datasets.keys())

# #TODO To move data collator       
# data_collator = DataCollatorForSeq2Seq(tokenizer, model=model)

# #just leave this
# tokenized_datasets = tokenized_datasets.remove_columns(
#     dataset_hf["train"].column_names
# )
# features = [tokenized_datasets["train"][i] for i in range(2)]
# data_collator(features)
# logger.info("Data ready for training.")



[nltk_data] Downloading package punkt to /home/petar/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package punkt_tab to /home/petar/nltk_data...
[nltk_data]   Package punkt_tab is already up-to-date!
2025-02-12 15:57:58.453 | INFO     | __main__:<module>:45 - Loaded dataset: smartcat/Amazon-2023-GenQ, name=
2025-02-12 15:58:05.889 | INFO     | __main__:<module>:60 - Selected  rows for "train" and for "test"


Map:   0%|          | 0/6169 [00:00<?, ? examples/s]

<class 'list'>
['NHL Molded Auto Emblem\n\nShowcase your team spirit with this eye-catching Chrome Finished Auto Emblem 3D Sticker by Rico Industries. This auto emblem 3D sticker measures 5-inches by 5-inches and is decorated with a dynamic and bold team logo. It easily adheres to any vehicle or other hard surface and is made of weather resistant materials. Made in the USA.', "Dickies Men's Short Sleeve Western Shirt\n\nDickies is the leading Global brand of innovative and trusted work wear. The brand has an unwavering commitment and proud heritage of providing tough, quality clothing to workers for more than 90 years. The Dickies brand has grown from bib overalls to world war ii u.S. Military uniforms to its iconic original 874 work pant, to footwear, and much more. Embraced by workers everywhere, Dickies is defined by the people who wear our apparel - independent, no nonsense and a little rough around the edges. As the signature brand in the portfolio owned by Williamson-Dickie MFG c

Map:   0%|          | 0/771 [00:00<?, ? examples/s]

<class 'list'>
['Bones Wheels Bones Skateboard Wheels 52mm Retros V3 Slims STF 99A White\n\nThese Bones wheels feature the V3 Slim shape. 52mm x 29mm, 99A. Bones Street Tech Formula powers the legendary Bones STF wheels that roll fast, grip when you need to and slide when you want to, without flat spotting. STF gives you more control to skate with confidence. Bones STF wheels outperform all other wheels, and because they wear so well, they last several times longer than normal wheels, making STF wheels the best for less.', "Skechers Men's Relaxed Fit: Expended-Bermo Oxford\n\nRound toe canvas lace up.", 'Party Ponies Miniature Horse/SM Pony Complete BITLESS Bridle - Many Colors!\n\nYOU\'VE ASKED FOR IT, AND HERE IT IS! BITLESS BRIDLE Brow band bridle with undropable snap on rein. MADE IN THE USA Fits Mini\'s and Ponies utilizing a bridle that measures 34" from bit port, around ears, to other side, at largest setting. 25" at smallest. Two-point adjustment. This bridle is not intended fo

2025-02-12 15:58:12.989 | INFO     | __main__:<module>:63 - Finished preprocessing tokenized dataset.


dict_keys(['train', 'test'])


In [18]:
tokenized_datasets["train"].column_names

['parent_asin',
 'main_category',
 'title',
 'description',
 'features',
 'embellished_description',
 'brand',
 'images',
 'short_query',
 'long_query',
 'input_ids',
 'attention_mask',
 'labels']